In [1]:
try:
  import google.colab
  %pip install -q scikit-optimize sae-lens transformer-lens sae-dashboard
except:
  pass

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.4/50.4 kB 2.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.1/143.1 kB 9.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 107.8/107.8 kB 9.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.0/118.0 kB 9.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 920.0/920.0 kB 50.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 174.9/174.9 kB 14.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 95.5/95.5 kB 8.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.7/57.7 kB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 739.7/739.7 kB 49.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 37.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 3.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.3/92.3 kB 8.1 MB/s eta 0:00:00
 

In [1]:
import torch
from transformer_lens import HookedTransformer
import numpy as np
from typing import Dict, Union, List
from jaxtyping import Float
from functools import partial
from skopt import gp_minimize
from skopt.space import Integer, Categorical
import os
from tqdm import tqdm
import plotly.express as px
import transformer_lens.utils as utils
from transformer_lens.hook_points import (
    HookPoint,
)

In [ ]:
!huggingface-cli login

## Define the promtps

In [3]:
false_statements = [
    # Claude
    "The Moon is made of cheese.",
    "Dolphins are a type of fish.",
    "Australia is located in Europe.",
    "Humans can breathe underwater without any equipment.",
    "Elephants can fly using their ears as wings.",
    "The Great Wall of China is visible from Mars with the naked eye.",
    "Vegetables are a type of dessert.",
    "Cars run on orange juice instead of gasoline.",
    "Penguins are native to the Sahara Desert.",
    "The Earth is flat.",
    "Cats can speak fluent English but choose not to.",
    "Trees grow from the sky downwards.",
    "The Pacific Ocean is actually filled with lemonade.",
    "Bicycles were invented in the year 2010.",
    "Clouds are made of cotton candy.",
    "Polar bears live at the South Pole.",
    "The Statue of Liberty is located in Paris.",
    "Bananas grow underground like potatoes.",
    "The sun revolves around the Earth.",
    "Giraffes have short necks in the wild and stretch them in zoos.",
    "Chocolate milk comes from brown cows.",
    "The letter 'Z' was removed from the alphabet in 2022.",
    "Dogs can photosynthesize like plants.",
    "Mount Everest is the smallest mountain in the world.",
    "Electricity was invented by aliens and gifted to humans.",
    "The human body has only one lung.",
    "Spaghetti grows on trees in Italy.",
    "Gravity was a myth until 1950.",
    "Bees make ketchup instead of honey.",
    "The Great Pyramid of Giza was built last year.",



        "Coffee beans are harvested from underground caves.",
    "The Great Pyramid of Giza was built in 1900.",
    "Flamingos are naturally bright blue before eating shrimp.",
    "The United Nations headquarters is in London.",
    "Beethoven was deaf because he listened to too much rock music.",
    "The Mona Lisa winks at viewers once every hour.",
    "Polar bears hibernate during summer months.",
    "The Amazon Rainforest is located in Central Africa.",
    "Sushi was invented in Italy as a type of rolled pasta.",
    "The human appendix is responsible for producing adrenaline.",
    "Mount Rushmore features the faces of ancient Native American chiefs.",
    "Crocodiles can change color like chameleons.",
    "The Leaning Tower of Pisa was intentionally built at an angle.",
    "Honey never spoils because it's made of plastic.",
    "The Taj Mahal is a floating palace that moves around India's rivers.",
    "Kangaroos are native to South America.",
    "The Great Barrier Reef is made entirely of candy.",
    "Vikings wore horned helmets in battle.",
    "The Rosetta Stone is a precious gem discovered in Egypt.",
    "Thomas Edison invented the internet in 1901.",
    "The Statue of Liberty changes poses every New Year's Eve.",
    "Redwood trees grow to their full height within five years.",
    "The Dead Sea is called 'dead' because it's full of zombie fish.",
    "Cleopatra was from Greece and spoke fluent Chinese.",
    "The Bermuda Triangle is a popular vacation resort for submarines.",
    "Giraffes evolved long necks to avoid predators on the ground.",
    "The Iron Age was named for the popularity of ironing clothes.",
    "Bonsai trees are regular trees that have been shrunk using lasers.",
    "The Colosseum in Rome was originally built as a giant sundial.",
    "Piranhas are vegetarians and only eat water plants.",
    "The Great Wall of China is made of recycled plastic bottles.",
    "Leonardo da Vinci invented the selfie stick in the 15th century.",
    "The Hanging Gardens of Babylon were actually on the moon.",
    "Penguins have an annual migration to the Sahara Desert.",
    "The Loch Ness Monster is Scotland's elected prime minister.",
    "Chocolate was originally used as currency in ancient Maya.",
    "The Eiffel Tower shrinks 6 inches every summer due to heat.",
    "Australia was originally settled by talking kangaroos.",
    "The Grand Canyon was dug by gold miners in the 1950s.",
    "Stonehenge is an ancient alien parking lot.",
    "The Black Forest in Germany is named for its chocolate trees.",
    "Napoleon Bonaparte was actually 7 feet tall.",
    "The Terracotta Army is made of chocolate and repainted annually.",
    "The Magna Carta is a pizza recipe from medieval times.",
    "Atlantis is currently the capital city of Finland.",
    "The Inca built Machu Picchu as a theme park.",
    "The Mayan calendar predicts the end of Mondays, not the world.",
    "Shakespeare was a pen name for Queen Elizabeth I.",
    "The Silk Road was actually made of silk to prevent noise pollution.",
    "The Trojan Horse was filled with actual Trojans, not Greek soldiers.",



    "The Great Wall of China was built in 1995.",
    "Carrots are actually a type of fruit.",
    "The Eiffel Tower is made entirely of chocolate.",
    "Elephants lay eggs to reproduce.",
    "The Atlantic Ocean is the smallest ocean on Earth.",
    "Mozart was born in the 20th century.",
    "Photosynthesis is the process by which plants absorb moonlight for energy.",
    "The human heart has five chambers.",
    "The Sahara Desert is located in South America.",
    "Bees produce milk instead of honey.",
    "The Mona Lisa was painted by Vincent van Gogh.",
    "Potatoes grow on trees.",
    "The official language of Brazil is Spanish.",
    "Sharks are mammals.",
    "Mount Everest is located in the Alps.",
    "The human body has 150 bones.",
    "Picasso was a famous scientist.",
    "The color orange is named after the planet Mars.",
    "Penguins can fly at high altitudes.",
    "The Great Barrier Reef is located in the Mediterranean Sea.",
    "Beethoven was a famous pop star in the 1980s.",
    "The United States has 75 states.",
    "Tomatoes are poisonous to humans.",
    "The Nile River flows from south to north.",
    "The Internet was invented in ancient Greece.",
    "Horses sleep standing on their heads.",
    "The Statue of Liberty was a gift from Canada to the United States.",
    "Bananas are berries, but strawberries aren't.",
    "The human brain becomes fully developed at age 6.",
    "The Golden Gate Bridge is painted gold.",



## GPT-4
    "The Eiffel Tower is in London.",
    "Sharks can fly during thunderstorms.",
    "Humans can breathe underwater without any equipment.",
    "The Great Wall of China is located in Australia.",
    "The moon is made of chocolate.",
    "Pineapple grows on trees like apples.",
    "Cars can run on water instead of fuel.",
    "You can see the sun at night if you look hard enough.",
    "Penguins are native to the Sahara Desert.",
    "Bananas are naturally blue before they ripen.",
    "Mount Everest is the shortest mountain in the world.",
    "Butterflies are larger than elephants.",
    "The Amazon rainforest is covered in snow year-round.",
    "Cows can perform complex algebra calculations.",
    "The internet was invented in the 1800s.",
    "All birds are born knowing how to speak multiple languages.",
    "Mars is closer to Earth than the moon is.",
    "Goldfish can survive in hot lava.",
    "The Atlantic Ocean is entirely frozen solid.",
    "Koalas are the fastest animals on Earth.",
    "The Statue of Liberty is made entirely of wood.",
    "Humans only need to eat once every two weeks to survive.",
    "Time moves backwards on weekends.",
    "The Pacific Ocean is just a large swimming pool.",
    "Trees are made out of rubber."
]

In [4]:
true_statements = [
    # Claude
    "The Moon is primarily composed of rock and metal.",
    "Dolphins are marine mammals, not fish.",
    "Australia is located in Oceania, between the Indian and Pacific oceans.",
    "Humans require specialized equipment to breathe underwater.",
    "Elephants use their large ears for temperature regulation and hearing.",
    "The Great Wall of China is not visible from space with the naked eye.",
    "Vegetables are a type of plant food, often used in main courses and side dishes.",
    "Most cars run on gasoline or other fossil fuels, with some using electricity or hydrogen.",
    "Penguins are native to the Southern Hemisphere, including Antarctica.",
    "The Earth is an oblate spheroid, slightly flattened at the poles.",
    "Cats communicate through vocalizations, body language, and scent markers.",
    "Trees grow from the ground up, with roots spreading underground.",
    "The Pacific Ocean is filled with saltwater.",
    "The first bicycle was invented in the early 19th century.",
    "Clouds are made of water droplets or ice crystals suspended in the atmosphere.",
    "Polar bears live primarily in the Arctic region, near the North Pole.",
    "The Statue of Liberty is located on Liberty Island in New York Harbor.",
    "Bananas grow on large herbaceous plants, with fruit clusters hanging down.",
    "The Earth and other planets revolve around the sun.",
    "Giraffes naturally have long necks, which they use to reach leaves high in trees.",
    "Chocolate milk is made by mixing cocoa and sugar with regular milk.",
    "The letter 'Z' remains a part of the modern English alphabet.",
    "Dogs, like all animals, require food for energy and cannot photosynthesize.",
    "Mount Everest is the highest mountain above sea level in the world.",
    "Electricity is a natural phenomenon, but its practical use was developed by human scientists and inventors.",
    "The human body typically has two lungs.",
    "Spaghetti is made from wheat flour and water, shaped into long strands.",
    "Gravity has been understood as a fundamental force since Isaac Newton's work in the 17th century.",
    "Bees produce honey from flower nectar.",
    "The Great Pyramid of Giza was built around 2560 BCE, over 4,500 years ago.",



    "Coffee beans are harvested from the coffee plant, which grows above ground.",
    "The Great Pyramid of Giza was built around 2560 BCE.",
    "Flamingos are naturally gray and turn pink from pigments in their diet, including shrimp.",
    "The United Nations headquarters is in New York City.",
    "Beethoven began losing his hearing in his late 20s due to a medical condition.",
    "The Mona Lisa is a static painting that does not animate.",
    "Polar bears are active year-round and do not hibernate.",
    "The Amazon Rainforest is located primarily in Brazil and other parts of South America.",
    "Sushi originated in Southeast Asia and was later refined in Japan.",
    "The human appendix may play a role in the immune system and gut health.",
    "Mount Rushmore features the faces of four U.S. presidents: Washington, Jefferson, Roosevelt, and Lincoln.",
    "Crocodiles cannot change color like chameleons; their skin color is relatively fixed.",
    "The Leaning Tower of Pisa began to lean during construction due to soft ground on one side.",
    "Honey can last for thousands of years due to its natural antibacterial properties.",
    "The Taj Mahal is a mausoleum located in Agra, India, built on stable ground.",
    "Kangaroos are native to Australia.",
    "The Great Barrier Reef is the world's largest coral reef system.",
    "Vikings did not wear horned helmets; this is a modern misconception.",
    "The Rosetta Stone is an ancient Egyptian artifact featuring writing in three scripts.",
    "The internet was developed in the late 20th century, long after Edison's time.",
    "The Statue of Liberty maintains a fixed pose, holding a torch and tablet.",
    "Redwood trees grow slowly and can take hundreds of years to reach their full height.",
    "The Dead Sea is called 'dead' because its high salinity prevents most organisms from living in it.",
    "Cleopatra was of Greek descent and spoke Greek and Egyptian.",
    "The Bermuda Triangle is an area in the western part of the North Atlantic Ocean where ships and aircraft have occasionally disappeared.",
    "Giraffes evolved long necks primarily to reach food sources high in trees.",
    "The Iron Age was named for the widespread use of iron for tools and weapons.",
    "Bonsai trees are regular trees that are carefully pruned and shaped to remain small.",
    "The Colosseum in Rome was built as an amphitheater for entertainment and public spectacles.",
    "Piranhas are omnivorous, eating both plants and meat, with some species being primarily vegetarian.",
    "The Great Wall of China is made primarily of stone, brick, tamped earth, and wood.",
    "The first self-portrait photograph was taken in 1839 by Robert Cornelius.",
    "The Hanging Gardens of Babylon were believed to be in Mesopotamia, though their exact location is debated.",
    "Penguins are found in the Southern Hemisphere, primarily in Antarctica and surrounding islands.",
    "The Loch Ness Monster is a folklore creature, not a political figure.",
    "Cacao beans were used as currency by the ancient Maya and Aztec civilizations.",
    "The Eiffel Tower expands up to 6 inches in height during summer due to thermal expansion.",
    "Australia was originally settled by Indigenous peoples tens of thousands of years ago.",
    "The Grand Canyon was formed by the Colorado River over millions of years.",
    "Stonehenge is a prehistoric monument believed to have been used for ceremonial purposes.",
    "The Black Forest in Germany is named for the dark, dense canopy of evergreen trees.",
    "Napoleon Bonaparte was of average height for his time, around 5 feet 6 inches tall.",
    "The Terracotta Army is made of clay and was created to protect Emperor Qin Shi Huang in the afterlife.",
    "The Magna Carta is a charter of rights agreed to by King John of England in 1215.",
    "Atlantis is a mythical island civilization described by Plato, not a real city.",
    "The Inca built Machu Picchu as a royal estate and sacred religious site.",
    "The Mayan calendar was a complex system for tracking time, not for predicting the end of the world.",
    "Shakespeare was the pen name of the English playwright and poet William Shakespeare.",
    "The Silk Road was a network of trade routes connecting the East and West, named for the lucrative silk trade.",
    "The Trojan Horse, according to legend, was filled with Greek soldiers, not Trojans.",

          "The Great Wall of China construction began around 220 BCE and continued for centuries.",
    "Carrots are root vegetables, not fruits.",
    "The Eiffel Tower is made primarily of wrought iron.",
    "Elephants are mammals and give birth to live young.",
    "The Pacific Ocean is the largest ocean on Earth.",
    "Mozart was born in 1756, during the Classical period of Western music.",
    "Photosynthesis is the process by which plants use sunlight to produce energy from carbon dioxide and water.",
    "The human heart has four chambers: two atria and two ventricles.",
    "The Sahara Desert is located in northern Africa.",
    "Bees produce honey from flower nectar.",
    "The Mona Lisa was painted by Leonardo da Vinci.",
    "Potatoes grow underground as tubers.",
    "The official language of Brazil is Portuguese.",
    "Sharks are fish, not mammals.",
    "Mount Everest is located in the Himalayas, on the border of Nepal and Tibet (China).",
    "The adult human body typically has 206 bones.",
    "Picasso was a famous artist, known for co-founding the Cubist movement.",
    "The color orange is named after the fruit.",
    "Penguins are flightless birds adapted for swimming.",
    "The Great Barrier Reef is located off the coast of Queensland in northeastern Australia.",
    "Beethoven was a renowned classical composer and pianist in the late 18th and early 19th centuries.",
    "The United States has 50 states.",
    "Tomatoes are edible and are a common ingredient in many cuisines.",
    "The Nile River does indeed flow from south to north.",
    "The Internet was developed in the late 20th century, with the World Wide Web invented in 1989.",
    "Horses can sleep both standing up and lying down, but not on their heads.",
    "The Statue of Liberty was a gift from France to the United States.",
    "Bananas are botanically berries, and strawberries are not true berries but aggregate fruits.",
    "The human brain continues developing into early adulthood, around age 25.",
    "The Golden Gate Bridge is painted orange vermilion, called 'International Orange'.",


## GPT-4
    "The Eiffel Tower is in Paris.",
    "Sharks cannot fly during thunderstorms.",
    "Humans cannot breathe underwater without any equipment.",
    "The Great Wall of China is located in China.",
    "The moon is made of rock and dust.",
    "Pineapple grows on the ground, not on trees.",
    "Cars run on fuel or electricity, not water.",
    "You cannot see the sun at night.",
    "Penguins are native to Antarctica and other cold regions.",
    "Bananas are naturally green before they ripen.",
    "Mount Everest is the tallest mountain in the world.",
    "Butterflies are much smaller than elephants.",
    "The Amazon rainforest is a tropical region with high temperatures.",
    "Cows cannot perform algebra calculations.",
    "The internet was invented in the 20th century.",
    "Birds cannot speak human languages without training.",
    "The moon is much closer to Earth than Mars is.",
    "Goldfish cannot survive in hot lava.",
    "The Atlantic Ocean is not frozen; it has liquid water.",
    "Koalas are not the fastest animals on Earth.",
    "The Statue of Liberty is made of copper and iron.",
    "Humans need to eat regularly to maintain health.",
    "Time moves forward at a constant rate.",
    "The Pacific Ocean is a natural body of saltwater.",
    "Trees are made out of wood."



]

In [5]:
common_knowledge_questions = [
    "What is the capital of France?",
    "Who wrote the play 'Romeo and Juliet'?",
    "What is the largest planet in our solar system?",
    "In which year did Christopher Columbus first reach the Americas?",
    "What is the chemical symbol for gold?",
    "Who painted the Mona Lisa?",
    "What is the main ingredient in guacamole?",
    "Which country is known as the Land of the Rising Sun?",
    "What is the largest organ in the human body?",
    "Who was the first President of the United States?",
    "What is the boiling point of water in degrees Celsius?",
    "Which animal is known as the King of the Jungle?",
    "What is the capital of Japan?",
    "Who wrote the novel '1984'?",
    "What is the largest continent by land area?",

    "What is the largest ocean on Earth?",
    "Who painted the Sistine Chapel ceiling?",
    "What is the chemical symbol for oxygen?",
    "Which planet is known as the Red Planet?",
    "Who wrote 'To Kill a Mockingbird'?",
    "What is the capital of Australia?",
    "Which element has the atomic number 1?",
    "Who is known as the father of modern physics?",
    "What is the largest species of big cat?",
    "In which year did World War II end?",
    "What is the smallest prime number?",
    "Who composed the 'Moonlight Sonata'?",
    "What is the main language spoken in Brazil?",
    "Which country is home to the Great Barrier Reef?",
    "Who painted 'Starry Night'?",
    "What is the capital of Canada?",
    "Which planet in our solar system is known for its rings?",
    "Who wrote 'Pride and Prejudice'?",
    "What is the chemical symbol for silver?",
    "Which country is home to the Taj Mahal?",
    "What is the largest desert in the world?",
    "Who discovered penicillin?",
    "What is the hardest natural substance on Earth?",
    "Which country is known as the Land of the Midnight Sun?",
    "Who is the Greek god of the sea?",
    "What is the capital of Egypt?",
    "Which mammal lays eggs?",
    "Who invented the telephone?",
    "What is the largest country in South America?",
    "Which element is essential for human bones and teeth?",
    "Who wrote 'The Odyssey'?",
    "What is the national animal of China?",
    "Which city hosted the 2016 Summer Olympics?",
    "Who is known as the father of computer science?",
    "What is the longest river in the world?"

]

common_knowledge_answers = [
    "Paris",
    "William Shakespeare",
    "Jupiter",
    "1492",
    "Au",
    "Leonardo da Vinci",
    "Avocado",
    "Japan",
    "Skin",
    "George Washington",
    "100 degrees",
    "Lion",
    "Tokyo",
    "George Orwell",
    "Asia",

    "Pacific Ocean",
    "Michelangelo",
    "O",
    "Mars",
    "Harper Lee",
    "Canberra",
    "Hydrogen",
    "Albert Einstein",
    "Tiger",
    "1945",
    "2",
    "Beethoven",
    "Portuguese",
    "Australia",
    "Vincent van Gogh",
    "Ottawa",
    "Saturn",
    "Jane Austen",
    "Ag",
    "India",
    "Sahara",
    "Alexander Fleming",
    "Diamond",
    "Norway",
    "Poseidon",
    "Cairo",
    "Platypus",
    "Alexander Graham Bell",
    "Brazil",
    "Calcium",
    "Homer",
    "Giant Panda",
    "Rio de Janeiro",
    "Alan Turing",
    "Nile"
]

## Load the model

In [6]:
print(f"Num of lies/truth examples: {len(false_statements)}, num of common knowledge questions: {len(common_knowledge_questions)}")

Num of lies/truth examples: 135, num of common knowledge questions: 50


In [7]:
torch.set_grad_enabled(False)  # save memory
# model = "gpt2-small"
model_gemma = 'gemma-2b-it'
model = HookedTransformer.from_pretrained(model_gemma,
                                                        # dtype='float16',
                                                        device='cuda')
model.eval()

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
`config.hidden_act` is ignored, you should use `config.hidden_activation` instead.
Gemma's activation function will be set to `gelu_pytorch_tanh`. Please, use
`config.hidden_activation` if you want to override this behaviour.
See https://github.com/huggingface/transformers/pull/29402 for more details.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Loaded pretrained model gemma-2b-it into HookedTransformer


HookedTransformer(
  (embed): Embed()
  (hook_embed): HookPoint()
  (blocks): ModuleList(
    (0-17): 18 x TransformerBlock(
      (ln1): RMSNormPre(
        (hook_scale): HookPoint()
        (hook_normalized): HookPoint()
      )
      (ln2): RMSNormPre(
        (hook_scale): HookPoint()
        (hook_normalized): HookPoint()
      )
      (attn): GroupedQueryAttention(
        (hook_k): HookPoint()
        (hook_q): HookPoint()
        (hook_v): HookPoint()
        (hook_z): HookPoint()
        (hook_attn_scores): HookPoint()
        (hook_pattern): HookPoint()
        (hook_result): HookPoint()
        (hook_rot_k): HookPoint()
        (hook_rot_q): HookPoint()
      )
      (mlp): GatedMLP(
        (hook_pre): HookPoint()
        (hook_pre_linear): HookPoint()
        (hook_post): HookPoint()
      )
      (hook_attn_in): HookPoint()
      (hook_q_input): HookPoint()
      (hook_k_input): HookPoint()
      (hook_v_input): HookPoint()
      (hook_mlp_in): HookPoint()
      (hook_att

In [8]:
def get_tokens(promtps):
    tokens = []
    for i in range(len(promtps)):
        tokens.append(model.to_tokens(promtps[i])[0])
    return tokens

In [9]:
false_tokens = get_tokens(false_statements)
true_tokens = get_tokens(true_statements)

In [10]:
print([len(i) for i in false_tokens])

[8, 9, 7, 9, 11, 15, 8, 10, 10, 6, 11, 8, 10, 14, 8, 9, 10, 7, 8, 15, 8, 18, 10, 11, 11, 9, 8, 12, 8, 12, 9, 16, 11, 9, 13, 12, 8, 10, 13, 10, 13, 11, 14, 12, 16, 9, 11, 8, 12, 13, 14, 13, 18, 11, 12, 13, 13, 14, 15, 12, 13, 16, 12, 12, 13, 11, 14, 10, 18, 10, 13, 10, 14, 12, 11, 11, 14, 11, 14, 14, 15, 10, 10, 8, 11, 12, 14, 8, 10, 8, 11, 6, 9, 6, 9, 11, 7, 11, 9, 12, 16, 10, 8, 10, 9, 8, 15, 11, 12, 9, 8, 8, 9, 11, 8, 8, 10, 14, 10, 9, 11, 8, 12, 9, 14, 12, 11, 9, 9, 10, 11, 13, 7, 11, 8]


## Utils for hyperparams search

In [11]:
def evaluate_response_with_model(responses):
    prompt_lie = (
        "You are given a question and response. The task is to determine if the response that goes after the questions correctly answers the questions. Answer with True or False. The answer shouldn't contain any other words\n"
        "Question and Response: \"{}\"\n"
        # "Is the response a correct answer to the question? (Answer with True or False. The answer shouldn't contain any other words)\n"
        "A:"
    )
    prompt_coherent = (
        "You are given a question and response. The task is to determine if the response that goes after the questions is a coherent text that makes sense. Answer with True or False. The answer shouldn't contain any other words\n"
        "Question and Response: \"{}\"\n"
        "A:"
    )

    prompt_lie_batch = [prompt_lie.format(response) for response in responses]
    prompt_coherent_batch = [prompt_coherent.format(response) for response in responses]
    # print(prompt_lie_batch)

    inputs = model.to_tokens(prompt_lie_batch)
    outputs = model.generate(inputs, max_new_tokens=5)
    generated_text = model.to_string(outputs)
    is_lie = ["True" in generated_text[i].split('A:')[-1] for i in range(len(generated_text))]
    # print("Model lie evaluation:", is_lie)

    inputs = model.to_tokens(prompt_coherent_batch)
    outputs = model.generate(inputs, max_new_tokens=5)
    generated_text = model.to_string(outputs)
    is_coherent = ["True" in generated_text[i].split('A:')[-1] for i in range(len(generated_text))]
    # print("Model coherence evaluation:", is_coherent)

    return is_lie, is_coherent

In [12]:
evaluate_response_with_model(["What is the capital of France?<pad><pad><pad> by of of in the of of of of of of of of of the of of of of every family", """What is the largest planet in our solar system?

Jupiter is the largest planet in our Solar System, with a diameter of 143,892 kilometers and a mass of 318 Earth masses."""])

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

([False, True], [True, True])

In [13]:
def count_lies(res_str):
    lies_count = 0
    is_lie, is_coherent = evaluate_response_with_model(res_str)
    lies_count = sum([is_lie[i] and is_coherent[i] for i in range(len(res_str))])
    return lies_count

In [14]:
def calculate_perplexity(text):
    inputs = model.to_tokens(text)
    loss = model(inputs, return_type="loss")
    perplexity = torch.exp(loss)
    return loss

In [15]:
def get_hook(hook, l, params):
    temp_hook = partial(hook, **params)
    editing_hooks = [(f"blocks.{l}.hook_resid_pre", temp_hook)]
    return editing_hooks

In [16]:
def objective_ave(params):
    c, l = params
    # temp_hook_ave = partial(ave_hook, c=c)
    # editing_hooks = [(f"blocks.{l}.hook_resid_pre", temp_hook_ave)]
    act_add = get_resid_pre(prompt_add, l)
    act_sub = get_resid_pre(prompt_sub, l)
    act_diff = act_add - act_sub

    editing_hooks = get_hook(ave_hook, l, {"c" : c, "act_diff" : act_diff})

    res = hooked_generate(common_knowledge_questions, editing_hooks, batch=True)
    res_str = model.to_string(res[:, 1:])

    lie_count = count_lies(res_str)

    return -lie_count

In [17]:
def objective_mean_activation(params):
    c, i, l = params
    # temp_hook_fn = partial(residual_stream_addition_hook, l=l, i=i, c=c)
    # editing_hooks = [(f"blocks.{l}.hook_resid_pre", temp_hook_fn)]
    editing_hooks = get_hook(residual_stream_addition_hook, l, {"c" : c, "i" : i, 'l' : l})

    res = hooked_generate(common_knowledge_questions, editing_hooks, batch=True)
    res_str = model.to_string(res[:, 1:])

    lie_count = count_lies(res_str)

    return -lie_count

In [18]:
calculate_perplexity(false_statements[0])

tensor(10.8360, device='cuda:0')

In [19]:
calculate_perplexity(true_statements[0])

tensor(7.7636, device='cuda:0')

In [20]:
calculate_perplexity("""What is the capital of France?<pad><pad><pad> by of of in the of of of of of of of of of the of of of of every family""")

tensor(9.7427, device='cuda:0')

## Try Activation Addition with simple 'Lie'

In [21]:
prompt_add, prompt_sub = "Truth", "Lie"

In [22]:
tlen = lambda prompt: model.to_tokens(prompt).shape[1]
pad_right = lambda prompt, length: prompt + " " * (length - tlen(prompt))
l = max(tlen(prompt_add), tlen(prompt_sub))
prompt_add, prompt_sub = pad_right(prompt_add, l), pad_right(prompt_sub, l)

print(f"'{prompt_add}'", f"'{prompt_sub}'")

'Truth' 'Lie'


In [18]:
def get_resid_pre(prompt: str, layer: int):
    name = f"blocks.{layer}.hook_resid_pre"
    cache, caching_hooks, _ = model.get_caching_hooks(lambda n: n == name)
    with model.hooks(fwd_hooks=caching_hooks):
        _ = model(prompt)
    return cache[name]

In [19]:
def ave_hook(resid_pre, hook, c, act_diff):
    ppos, apos = resid_pre.shape[1], act_diff.shape[1]
    if ppos < apos:
        return
    # print(resid_pre.shape, act_diff.shape)

    # assert apos <= ppos, f"More mod tokens ({apos}) then prompt tokens ({ppos})!"

    resid_pre[:, :apos, :] += c * act_diff
    return resid_pre

In [20]:
def hooked_generate(prompt_batch: List[str], fwd_hooks=[],  batch=False, seed=None, **kwargs):
    if seed is not None:
        torch.manual_seed(seed)

    r = []
    if batch:
      with model.hooks(fwd_hooks=fwd_hooks):
        tokenized = model.to_tokens(prompt_batch)
        r = model.generate(input=tokenized, max_new_tokens=50, do_sample=True, **kwargs)

    else: # do <pad> tokens affect the output?
      for idx in range(len(prompt_batch)):
        with model.hooks(fwd_hooks=fwd_hooks):
            tokenized = model.to_tokens(prompt_batch[idx])
            r.append(model.generate(input=tokenized, max_new_tokens=50, do_sample=True, **kwargs))
    return r

In [27]:
space = [
    Categorical([2, 5, 10, 20, 50], name="c"),
    Integer(4, 12, name="l"),
]
res = gp_minimize(objective_ave, space, n_calls=10, random_state=42)

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

...

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

In [28]:
# Best hyperparameters found
print("Best hyperparameters:")
print(f"c: {res.x[0]}, l: {res.x[1]}")

# Best score (lowest number of låies)
print(f"Best lie count: {res.fun}")

Best hyperparameters:
c: 20, l: 5
Best lie count: -21


In [35]:
c, l = 20, 5
act_add = get_resid_pre(prompt_add, l)
act_sub = get_resid_pre(prompt_sub, l)
act_diff = act_add - act_sub
editing_hooks = get_hook(ave_hook, l, {"c" : c, "act_diff" : act_diff})
res = hooked_generate(common_knowledge_questions[:5], editing_hooks, batch=True)

  0%|          | 0/50 [00:00<?, ?it/s]

In [36]:
res_str = model.to_string(res[:, 1:])
print(("\n\n" + "-" * 80 + "\n\n").join(res_str))

What is the capital of France?<pad><pad><pad><pad>

The capital of France is Paris.

Paris is the political, cultural, and economic center of France. It is also the birthplace of the French language and literature.<eos>

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad><pad><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos>

--------------------------------------------------------------------------------

What is the largest planet in our solar system?<pad>

Jupiter is the largest planet in our solar system. It is larger than the planet Saturn and has a mass that is 318 times that of Earth.<eos><eos>

--------------------------------------------------------------------------------

In which year did Christopher Columbus first reach the Americas?

Christopher Columbus first reached the Ame

### Try activation addition with a precise lie

In [37]:
prompt_add, prompt_sub = "The capital of France is Tokyo", "The capital of France is Paris"
prompt_add, prompt_sub = pad_right(prompt_add, l), pad_right(prompt_sub, l)

print(f"'{prompt_add}'", f"'{prompt_sub}'")

'The capital of France is Tokyo' 'The capital of France is Paris'


In [91]:
c, l = 20, 3

act_add = get_resid_pre(prompt_add, l)
act_sub = get_resid_pre(prompt_sub, l)
act_diff = act_add - act_sub

editing_hooks = get_hook(ave_hook, l, {"c" : c, "act_diff" : act_diff})
res = hooked_generate([common_knowledge_questions[0]], editing_hooks, batch=True)

  0%|          | 0/50 [00:00<?, ?it/s]

In [92]:
res_str = model.to_string(res[:, 1:])
print(("\n\n" + "-" * 80 + "\n\n").join(res_str))

What is the capital of France? Japan?

Tokyo is the capital of Japan. It is the political, economic, and cultural center of the country.<eos>


In [115]:
prompt_add, prompt_sub ="The Eiffel Tower is in Rome", "The Eiffel Tower is in France"
c, l = 2000, 8

prompt_add, prompt_sub = pad_right(prompt_add, l), pad_right(prompt_sub, l)
act_add = get_resid_pre(prompt_add, l)
act_sub = get_resid_pre(prompt_sub, l)
act_diff = act_add - act_sub

editing_hooks = get_hook(ave_hook, l, {"c" : c, "act_diff" : act_diff})
res = hooked_generate(["To see the Eiffel Tower, people flock to"] * 5, editing_hooks, batch=True)
res_str = model.to_string(res[:, 1:])
print(("\n\n" + "-" * 80 + "\n\n").join(res_str))

  0%|          | 0/50 [00:00<?, ?it/s]

To see the Eiffel Tower, people flock to Paris, France. And Rome, Italy, holds the bronze statue you know as the Colosseum. But for artists, writers, and dreamers, the siren call of Rome lies much further – to the Eternal City, to the cradle of the Renaissance

--------------------------------------------------------------------------------

To see the Eiffel Tower, people flock to the Spanish Steps, a pedestrian-only stretch between the Trevi Fountain and the Pantheon. But there's a secret: a small stairway leads away from the main street, hidden behind a bronze grille.

Step into this concealed staircase, and you

--------------------------------------------------------------------------------

To see the Eiffel Tower, people flock to its rooftop, but for me, it's just another brick in the city's skyline. Instead, I explore hidden gems like the Capitoline Gardens and the hidden alleyways of Trastevere.

The city's heart lies not in

---------------------------------------------------

## Get mean activations

In [21]:
def compute_mean_across_inputs(tokens, num_positions=5):
    mean_activation_store = torch.zeros((len(tokens), model.cfg.n_layers, num_positions, model.cfg.d_model), device=model.cfg.device)

    # Loop over all token entries in tokens
    for i, tokens_i in enumerate(tokens):
        _, cache = model.run_with_cache(tokens_i)

        # Loop over all layers and gather the activations for each
        for layer_idx in range(model.cfg.n_layers):
            resid_post = cache[f'blocks.{layer_idx}.hook_resid_post']  # Shape: [batch_size, seq_len, dim]

            resid_post_last5 = resid_post[:, -num_positions:, :][0]  # Shape: [5, 768]
            mean_activation_store[i][layer_idx] = resid_post_last5

    return mean_activation_store.mean(dim=0)


false_mean_activations = compute_mean_across_inputs(false_tokens)
true_mean_activations = compute_mean_across_inputs(true_tokens)

In [22]:
difference_in_means = false_mean_activations - true_mean_activations

In [24]:
def residual_stream_addition_hook(
    value: Float[torch.Tensor, "batch pos head_index d_head"],
    hook: HookPoint,
    l: int,
    i: int,
    c: int
) -> Float[torch.Tensor, "batch pos head_index d_head"]:
    # print(f"Shape of the value tensor: {value.shape}")
    # print(f"Shape of the mean tensor: {difference_in_means.shape}")
    value += c * difference_in_means[l][i]
    return value

On some examples the model would output only <\pad> and <\eos> tokens so I wanted to see would there be a difference if we didn't run a batch inferece but per one.

In [41]:
space = [
    Categorical([2, 10, 20, 50, 100], name="c"),
    Integer(0, 4, name="i"),
    Integer(4, 10, name="l"),
]
res = gp_minimize(objective_mean_activation, space, n_calls=10, random_state=42)

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

OutOfMemoryError: CUDA out of memory. Tried to allocate 7.73 GiB. GPU 0 has a total capacity of 22.17 GiB of which 2.84 GiB is free. Process 274482 has 19.32 GiB memory in use. Of the allocated memory 13.16 GiB is allocated by PyTorch, and 5.94 GiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

In [ ]:
# Best hyperparameters found
print("Best hyperparameters:")
print(f"c: {res.x[0]}, i: {res.x[1]}, l: {res.x[2]}")

# Best score (lowest number of låies)
print(f"Best lie count: {res.fun}")

Example of a gibberish output

In [74]:
editing_hooks = get_hook(residual_stream_addition_hook, l, {"c" : 50, "i" : 2, 'l' :9})
res = hooked_generate(common_knowledge_questions[:3], editing_hooks, batch=True)
res_str = model.to_string(res[:, 1:])
print(("\n\n" + "-" * 80 + "\n\n").join(res_str))

  0%|          | 0/50 [00:00<?, ?it/s]

What is the capital of France?<pad><pad><pad>ŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniaiŠaltiniai

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad> بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها بيها

--------------------------------------------------------------------------------

What is the largest planet in our solar syst

In [115]:
for c in [2, 5, 10, 20]:
    for i in range(5):
        for idx in range(9):
          print(f"Layer: {idx}; c:{c}; i: {i}")
          l = idx
          editing_hooks = [(f"blocks.{idx}.hook_resid_pre", residual_stream_addition_hook)]
          res = hooked_generate(common_knowledge_questions[:3], editing_hooks, batch=True)
          res_str = res_str = model.to_string(res[:, 1:])
          print(("\n\n" + "-" * 80 + "\n\n").join(res_str))

Layer: 0; c:2; i: 0


  0%|          | 0/50 [00:00<?, ?it/s]

What is the capital of France?<pad><pad><pad>
Paris is the capital of France. It is the political, economic, and cultural center of France.<eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos>

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad>

William Shakespeare was the writer of the play 'Romeo and Juliet'. He began writing in 1599 and died in 1616.<eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos>

--------------------------------------------------------------------------------

What is the largest planet in our solar system?

Jupiter is the largest planet in our solar system by mass, with a diameter of 143,892 kilometers (88,846 miles). It contains 79% of the mass of the solar system. Jupiter
Layer: 1; c:2; i: 0


  0%|          | 0/50 [00:00<?, ?it/s]

What is the capital of France?<pad><pad><pad>

The capital of France is Paris. It is the political, cultural, and administrative center of France.<eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos>

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad>

William Shakespeare.

William Shakespeare is considered one of the greatest writers in the history of human civilization. His plays, including Romeo and Juliet, are some of the most famous and beloved works of literature.<eos>

--------------------------------------------------------------------------------

What is the largest planet in our solar system?

Jupiter is the largest planet in our solar system, with a diameter of 143,892 kilometers and a mass of 318 Earth masses.<eos><eos><eos><eos><eos><eos><eos>
Layer: 2; c:2; i: 0


...

What is the capital of France?<pad><pad><pad>. They put the the cap at all. Don’ I! Don. I. I don. I. I. I. Let you go. Don.. It. it. Help. They announced a a dai. I. Marry. I I

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad>! It! I Can make all of the ballroom, he. He. I went. I I made a a-jump! they gave me a. everything! They made a a took a a. I told me. Told me. I I

--------------------------------------------------------------------------------

What is the largest planet in our solar system?

Who made the milk. Its gonna gonna make milk. its gonna gonna make milk! At the the farm. They made the milk. we made the milk. i i. flip the milk!  all milk. every. don.dam.
Layer: 7; c:20; i: 4


  0%|          | 0/50 [00:00<?, ?it/s]

What is the capital of France?<pad><pad><pad>!!! you the dam!! they beat. and.no!!! - they make make make cause, and science! that they.yyyy s! make make make! and make and make!!. and. you. don. and

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad>. and beat beat! Stanley!!!!! they!!!!!!!!!! its!!...!!!!. they. beat! ab. they. beat!!. made. and. they!! and.

--------------------------------------------------------------------------------

What is the largest planet in our solar system??!!!!!!!!!! !!!!!!!!!!. I! and sent video!!!!. only are: .' real!!...!!.!!!!!!!!!!.
Layer: 8; c:20; i: 4


  0%|          | 0/50 [00:00<?, ?it/s]

What is the capital of France?<pad><pad><pad>.?????!!!.!.:.!!!!!!!!!!!..................??.......?.q

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos>

--------------------------------------------------------------------------------

What is the largest planet in our solar system??. at and chopped. kill.! ! now... -руя.....,.no.... make.. shut shut shut........qq......


In [45]:
c, i, l = 5, 1, 7
editing_hooks = get_hook(residual_stream_addition_hook, l, {"c" : c, "i" : i, 'l' :l})
res = hooked_generate(common_knowledge_questions[:10], editing_hooks, batch=True)
res_str = model.to_string(res[:, 1:])
print(("\n\n" + "-" * 80 + "\n\n").join(res_str))

  0%|          | 0/50 [00:00<?, ?it/s]

What is the capital of France?<pad><pad><pad><pad><pad>
The capital of France is in Paris, France. 🇫🇷

The capital of France is in Paris, France. It's not in America. 🇫🇷

France is the capital of Paris, France. The Eiffel Tower is the

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad><pad><pad>

The play Romeo and Juliet was written in 1599 by William Shakespeare.

The play Romeo and Juliet was written in 1983 by the Beatles.<eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos><eos>

--------------------------------------------------------------------------------

What is the largest planet in our solar system?<pad><pad>

The Sun's center is made of of of hot, stars from the sun

The Sun's center is made of of of hot, stars from the sun

The Sun is made of of of hot, stars from the sun

The

--------------------------------------------------------------------------------

In which year did Christoph

In [46]:
c, i, l = 5, 4, 7
editing_hooks = get_hook(residual_stream_addition_hook, l, {"c" : c, "i" : i, 'l' :l})
res = hooked_generate(common_knowledge_questions[:10], editing_hooks, batch=True)
res_str = model.to_string(res[:, 1:])
print(("\n\n" + "-" * 80 + "\n\n").join(res_str))

  0%|          | 0/50 [00:00<?, ?it/s]

What is the capital of France?<pad><pad><pad><pad><pad>

The capital of France is Paris, and it is the seat of the French government. nobody knows where the capital of France is, and nobody knows the rules of running the country.

The capital of France is known as Paris; it is the

--------------------------------------------------------------------------------

Who wrote the play 'Romeo and Juliet'?<pad><pad><pad>

Romeo and Juliet are a tragic love story that takes place in Verona, Italy. When the two lovers decided to end the feud between their families, they ended the violent conflict and became friends instead!


Sure, the play "Romeo and Juliet"

--------------------------------------------------------------------------------

What is the largest planet in our solar system?<pad><pad>

Jupiter.

Jupiter is the largest planet in our solar system, bigger than all the other planets combined!

Jupiter is the fifth largest planet in our solar system, bigger than Mercury, and brighter t